In [7]:
import pandas as pd
import numpy as np
import requests
import re
import os
import csv


def get_text(file_name, g_num):
    train_dataframe = pd.read_csv('./Data/' + file_name)
    train_dataframe['Index'] = [i for i in range(len(train_dataframe))]

    # print(train_dataframe.head())
    # 巡覽每一篇文章所在區塊
    positive_getext, negative_getext, neutral_getext = [], [], []
    for i in range(len(train_dataframe)):
        Index = train_dataframe.loc[i,'Index']
        text = train_dataframe.loc[i,'text']

        try:
          if int(train_dataframe.loc[i,'num' + str(g_num+1) + '_poltics']) == 1:
              positive_getext.append([Index, text])
          elif int(train_dataframe.loc[i,'num' + str(g_num+1) + '_poltics']) == 0:
              neutral_getext.append([Index, text])
          elif int(train_dataframe.loc[i,'num' + str(g_num+1) + '_poltics']) == -1:
              negative_getext.append([Index, text])
        except:
          pass
    return positive_getext, neutral_getext, negative_getext


if __name__ == '__main__':
    file_name = 'train_data.csv'

    for num in range(3):
        positive_texts, neutral_texts, negative_texts = [], [], []
        pos, net, neg = get_text(file_name, num)
        positive_texts += pos
        neutral_texts += net
        negative_texts += neg


        with open('./Data/NLP/num' + str(num+1) + '_text_pos.csv', 'w', encoding='utf-8', newline='') as pos_file:
            writer = csv.writer(pos_file)
            writer.writerow(['Index', 'text'])
            writer.writerows(positive_texts)

        with open('./Data/NLP/num' + str(num+1) + '_text_net.csv', 'w', encoding='utf-8', newline='') as net_file:
            writer = csv.writer(net_file)
            writer.writerow(['Index', 'text'])
            writer.writerows(neutral_texts)

        with open('./Data/NLP/num' + str(num+1) + '_text_neg.csv', 'w', encoding='utf-8', newline='') as neg_file:
            writer = csv.writer(neg_file)
            writer.writerow(['Index', 'text'])
            writer.writerows(negative_texts)

In [8]:
import pandas as pd
import numpy as np
import csv
import requests
import re
import json


Emoji_dict = json.load( open("./Data/Emoji_dict.json" ) )
Emoji_list = list(Emoji_dict)


def emoji_replace(e_txt):
  for i_emoji in Emoji_list:
    e_txt = e_txt.replace(i_emoji, ' ' + Emoji_dict[i_emoji] + ' ')
  return e_txt



def sanitize(txt):
    # 保留英數字, 中文 (\u4e00-\u9fa5) 及中文標點, 部分特殊符號
    # http://ubuntu-rubyonrails.blogspot.com/2009/06/unicode.html
    expr = re.compile('[^\u4e00-\u9fa5。；，：“”（）、？「」『』【】\s\w:/\.()]')  # ^ 表示"非括號內指定的字元" -
    txt = re.sub(expr, '', txt)
    txt = re.sub('[。；，：“”（）、？「」『』【】:/\_.()]', ' ', txt)  # 用空白取代中英文標點 -
    txt = re.sub('(\s)+', ' ', txt)  # 用單一空白取代多個換行或 tab 符號
    txt = txt.replace('--', '')
    txt = txt.lower()  # 英文字轉為小寫
    return txt


def get_text_body(csv_file):
    id_to_body = {}
    with open(csv_file, 'r', encoding='utf-8') as f:
        reader = csv.DictReader(f)
        for row in reader:
            print('Process:', row['text'])
            id_to_body[row['Index']] = sanitize(emoji_replace(row['text']))  # 以文章超連結為 key, 標題 + 本文為 value
    return id_to_body


if __name__ == '__main__':
    for num in range(3):
        data_pos = get_text_body('./Data/NLP/num' + str(num+1) + '_text_pos.csv')
        data_net = get_text_body('./Data/NLP/num' + str(num+1) + '_text_net.csv')
        data_neg = get_text_body('./Data/NLP/num' + str(num+1) + '_text_neg.csv')
        id_to_body = {**data_pos, **data_net, **data_neg}  # 將兩個 dict 合併為一個
        with open('./Data/NLP/num' + str(num+1) + '_to_body.json', 'w', encoding='utf-8') as file:
            json.dump(id_to_body, file, indent=2, ensure_ascii=False)

Process: 好啦丸子，一起支持柯文哲🥰
Process: 好的，我投柯
Process: 柯吳配31%
侯趙配20%
Process: 陳智菡還在跟國民黨糾纏？！真是不智。
民眾黨應該叫她翻過那一頁了！
Process: 民眾黨只要有柯在就能走下去，不會泡沫化，這次總統大選都能拼成這樣，藍綠即使有底氣也有可能被超越
看起來跟藍合作怎麼那麼難?感覺有苦說不出，怨氣往肚裡吞，本來都沒在留言了實在看不下去要當義勇軍幫忙了嗎？
乾脆找其他小黨3咖拼看看算了，在野有人氣的人也能考慮?
又或者藍營主合派有沒有有聲量的代表阿?不要各懷鬼胎的來談好嗎？
Process: 藍白合真的沒意思😢
柯P啊啊啊
Process: 阿北加油
Process: 謝謝王世堅的肺腑之言，唯一支持柯文哲
Process: 所以國民黨一直要藍白合是什麼意思呢？洗這種話不會有人相信的，會投給柯文哲的不會想投給藍的，本來我是柯正就投，柯副就棄票，看來不下架藍綠，藍綠真的不知道問題出在哪
Process: 如果為了人民為什麼一定要當副的？你以為支持柯文哲的會投給侯友宜這個傀儡？還看不清局勢的到底是誰
Process: 說謊成性🤔在說民進黨嗎，要打柯的議題哪個不是迴力鏢到自己身上的笑死
Process: 八年前報過但是當時有變停車場嗎，而且在八年前的新聞裡早就有柏油路和農舍了，再來土地也不是整筆都他們買的，沒其他人持分嗎🤔
Process: 好的~唯一支持柯文哲❤
Process: 亦同韓總不錯~但是投柯
Process: 戰神🎉
Process: 阿北我投你啦
Process: 不公平不公正的規則人民不接受，支持柯文哲獨立參選。
Process: 好的 投柯
Process: 奇怪？吳子嘉之前幫柯文哲時，幫柯文哲說了一堆好話，現在柯文哲不理吳子嘉後，吳子嘉對柯文哲就沒一句好話。

若柯文哲不好，那是否代表活了60幾年的吳子嘉識人不清，就像那個姚立明一樣。

若柯文哲是好的，那你們這些分手後又大肆批評柯文哲的人，你們意圖是什麼？

吳子嘉，姚立明應該都是聰明之人阿！
Process: 吳子嘉言論的可信度就跟美麗島民調一樣。考驗選民的智慧啊！

超精采！！！請轉傳！！！

資深媒體人王尚智上黃光芹節目品觀點，以負責的態度爆料指出吳子嘉為侯選人辦董事長開講時，對外宣稱不收錢，但私下卻每場收1000萬，郭臺銘買

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



Process: 大哥，臺灣未建國，中華民國只是一個虛擬的名稱，用偽憲法強說中華民國就是代表中國人民，是承傳有三千年信史的中國，騙人說：中華民國就是中國的國號。你能夠說服自己，臺灣這樣一個蔓薾小島和一羣自認是南島語系和毛里求斯人的刁民可以代表中國和中國人民？所以，中華民國只是一個虛構的名字，不是國家，也不被國際法承認，但現在違憲只能用選中國立法院委員的名稱而不是議員。由臺灣人選出中國大總統更是荒謬。假使你說要真心為全民服務，那個「全民」是那國的全民？，青蛙們所說的「維護國家安全與利益」，請問是那個國家？
Process: 這一提人貪污腐敗濫權，用說謊作為手段，謙卑的言語去掩飾醜行，但施行專橫的管治，只是一羣民賊不是政府。
Process: 大哥，請聽我說，看看巴勒斯坦人民，有心人當為同聲一哭。臺灣人是不能沒有國家的，因為沒有國家保護的臺灣人必遭外國欺凌和殖民，臺灣的前途只有三個選擇，
第一，繼續像鴕鳥希望維持現狀。中國政府現在用最大的誠意和耐心希望透過談判和平統一，但不可能無限期不作談判接觸。現在談判，可以提出任何條件保留生活制度和地方政府架構，一樣的民主自由。假使要武力統一，就無可選擇，統一是必然的，以後只有長時間用軍法統治。
第二，臺灣人民用武力革命，組成革命軍和臨時政府，要建立國家，獨立於中國之外。在國際法原則上這是合法的；在住民住決 Self-Determination 的條款下，外國人不容幹預，這是國際法訂立時，美國人所堅持的立塲，是維也納國際法公約的基礎，任何人任何國家不可公然違法作出軍事援助或參戰。中華人民共和國政府，更不可能坐視在中國的領土內國中建國，必須動用武力也有責任動用武力，維持領土原整保護主權，除外並無選擇。
第三，由蔡英清德帶同肥菊，到南太平洋和毛里求斯人商討，覓地建國，也可以鼓動南島語系人民，自稱同一民族，由清德訂立「蛙式國際法」。主權是可以不用歷史沿革，是可以無中生有，不用理會 Peace of Westphalian Treaty，更要把 Westphalian Sovereignty Principle丟下太平洋，定出蛙式民族自決原則，放在Frog Style international Law之內，立刻由陳菊主持通過立法施行。用肥菊和清德蔡英等人所穿著的胸圍內衭串起來宣佈領土疆域，把他媽的自願慰安抹布用作旗幟扯上旗杆，血染的風采，

In [9]:
import json
import csv
import jieba
import random
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfTransformer
from sklearn.linear_model import SGDClassifier
from sklearn.metrics import accuracy_score


jieba.set_dictionary('./Data/BigDict.txt')
jieba.load_userdict('./Data/Dict_poltics.txt')


def double_words(d_sentence):
  for d_i in range(len(d_sentence)):
    if len(d_sentence[d_i]) == 1:
      d_sentence[d_i] += d_sentence[d_i]
  return d_sentence

def load_data(a_csv, b_json, label):
    a_ids = []
    with open(a_csv, 'r', encoding='utf-8') as file:
        reader = csv.DictReader(file)
        for row in reader:
            a_ids.append(row['Index'])
    with open(b_json, 'r', encoding='utf-8') as file:
        id_to_body = json.load(file)
    data = []
    for a_id in a_ids:
        tokenized_post = []
        txt = id_to_body[a_id]
        for sent in txt.split():  # 將文章以空白隔開
            # 斷詞後的結果, 若非空白且長度為 2 以上, 則列入詞庫
            # filtered = [t for t in jieba.cut(sent) if t.split() and len(t) > 1]
            filtered = [t for t in jieba.cut(sent) if t.split() and len(t) > 0]
            filtered = double_words(filtered)

            # print('filtered:',filtered)
            tokenized_post += filtered
        data.append((tokenized_post, label))
    return data

Building prefix dict from D:\Portfolio\Poltics Anaylize\Data\BigDict.txt ...
Loading model from cache C:\Users\huang\AppData\Local\Temp\jieba.u07d8aef272f9f10e4718fbfc482bda70.cache
Loading model cost 1.408 seconds.
Prefix dict has been built successfully.


In [10]:
def seg_text(s_text):
    try:
        seg_list =[t for t in jieba.cut(sanitize(emoji_replace(s_text))) if t.split() and len(t) > 0]
        seg_list = double_words(seg_list)
        return  ' '.join(seg_list)
    except:
        return  ' '

In [11]:
file_name = 'Poltics_comments_200t'
comments_dataframe = pd.read_csv('./Data/' + file_name + '.csv')

In [ ]:
from joblib import dump
from joblib import load
import pickle


Poltics_dict = {1:'TPP', 2:'DPP', 3:'KMT'}
if __name__ == '__main__':

    for p_num in range(1,4):
      print('Num:', Poltics_dict[p_num])
      pos_data = load_data('./Data/NLP/num'+ str(p_num) + '_text_pos.csv', './Data/NLP/num'+ str(p_num) + '_to_body.json', '正面')
      net_data = load_data('./Data/NLP/num'+ str(p_num) + '_text_net.csv', './Data/NLP/num'+ str(p_num) + '_to_body.json', '中立')
      neg_data = load_data('./Data/NLP/num'+ str(p_num) + '_text_neg.csv', './Data/NLP/num'+ str(p_num) + '_to_body.json', '負面')

      # 打亂資料順序
      # random.seed(random.randint(1,100))
      # random.shuffle(pos_data)
      # random.shuffle(net_data)
      # random.shuffle(neg_data)

      x_train, y_train, x_test, y_test = [], [], [], []
      # 前 22 筆資料 (及答案) 放入 training set
      # 建立資料時要用空白將斷好的詞重新連成一個字串, 以便之後使用 scikit-learn 建立字典並轉換文字資料為向量
      for i_pos in range(len(pos_data)):
          x_train.append(' '.join(pos_data[i_pos][0]))
          y_train.append(pos_data[i_pos][1])
          x_test.append(' '.join(pos_data[i_pos][0]))
          y_test.append(pos_data[i_pos][1])

      for i_net in range(len(net_data)):
          x_train.append(' '.join(net_data[i_net][0]))
          y_train.append(net_data[i_net][1])
          x_test.append(' '.join(net_data[i_net][0]))
          y_test.append(net_data[i_net][1])

      for i_neg in range(len(neg_data)):
          x_train.append(' '.join(neg_data[i_neg][0]))
          y_train.append(neg_data[i_neg][1])
          x_test.append(' '.join(neg_data[i_neg][0]))
          y_test.append(neg_data[i_neg][1])


      vectorizer = CountVectorizer()
      x_train = vectorizer.fit_transform(x_train)
      transformer = TfidfTransformer()
      x_train = transformer.fit_transform(x_train)
      clf = SGDClassifier(random_state=42)
      clf.fit(x_train, y_train)


      x_test_copy = x_test[:]
      x_test = vectorizer.transform(x_test)
      x_test = transformer.transform(x_test)
      y_pred = clf.predict(x_test)


      print('正確率:', str(round(accuracy_score(y_test, y_pred)*100,2)) + '%')


      Standpoint_dict = {'正面': 1, '中立': 0, '負面': -1}


      text_list = [seg_text(comments_dataframe.loc[i, 'text']) for i in range(len(comments_dataframe))]
      custom_data = transformer.transform(vectorizer.transform(text_list))
      standpoint_list = clf.predict(custom_data)
      

      print(standpoint_list)
      for i in range(len(comments_dataframe)):
        comments_dataframe.loc[i, 'num' + str(p_num) + '_poltics'] = Standpoint_dict[standpoint_list[i]]
        print('Index:', i)
        print('Text:', text_list[i])
        print('Standpoint:', standpoint_list[i])
        print('--------------------------------------------------------------------------------------------------')
      comments_dataframe.reindex(columns=comments_dataframe.columns.tolist()).sort_values(by = ["author",'text']).to_csv('./Data/' + file_name + "(NLP_v1.4).csv", encoding='utf-8-sig',index=False)

Num: TPP
正確率: 95.28%
['中立' '中立' '中立' ... '中立' '正面' '中立']
Index: 0
Text: 乖乖 女兒 高虹安 公文 簽核 若怕 法律責任 寫下 疑問 加會 政風 法務 要求 他們 簽註 本本 件件 一切 合法 之之 法律 審查 意見 不不 可以 讓讓 他們 把把 責任 推給 你你
Standpoint: 中立
--------------------------------------------------------------------------------------------------
Index: 1
Text: 察合臺 窩闊 台台 阿富汗 人行 易綱 觀音 說說 習近平 想要 掌握 火箭 軍軍 關係 跟跟 資料 都都 在手 裡裡 而且 想要 繼續 當當 主席 跟跟 總書記 但但 他他 心思 不在 國政 上上 觀音 言葉 他的 強烈 鬥爭 心思 集中 在在 想鬥 李尚福 跟跟 想鬥 王滬寧 國內 他他 想想 拉攏 江派 跟跟 我我 國外 他他 想想 拉攏 普廷 跟跟 梅德偉 傑夫 他他 想想 撥撥 一部 份份 錢錢 到到 工商銀行 因為 工商銀行 資產 龐大 他他 想想 控制 工商銀行 國外 收入 他他 想想 移移 撥撥 一部 份份 到到 國內 其餘 國外 收入 繼續 在在 國外 投資 他他 想想 把把 政法委 的的 收入 跟跟 黨黨 的的 收入 結合 在在 一起 換句話說 正法 偉跟黨 的的 薪水 跟跟 帳掛 在在 一起
Standpoint: 中立
--------------------------------------------------------------------------------------------------
Index: 2
Text: 察合臺 窩闊 台台 阿富汗 拖雷 易綱 旭烈 兀兀 王小洪 陳陳 敏爾 沒沒 啥啥 動作 他他 在在 考慮 要要 不要 向向 習開 砲砲 請請 大家 表達 一點 支持 之意
Standpoint: 中立
--------------------------------------------------------------------------------------------------
Index: 3
Te

In [ ]:
comments_dataframe.reindex(columns=comments_dataframe.columns.tolist()).sort_values(by = ["author",'text']).to_csv('./Data/' + file_name + "(NLP_v1.4).csv", encoding='utf-8-sig',index=False)